# Lyrics Analysis

In [439]:
lyrics_directory = "Lyrics_Data/"
tracks_csv = "tracks_group.csv"
stopwords_file = "stopwords.txt"

In [440]:
target_group = "kpop"
kpop_group = set(['kpop', 'itzy', 'seventeen', 'bts', 'twice'])
global_group = set(['global', 'billboard'])

target_and_kpop = kpop_group.union(set([target_group]))
target_and_global = global_group.union(set([target_group]))

## Import data

In [441]:
import pandas as pd

In [442]:
df = pd.read_csv(tracks_csv)

df.head(3)

track_name                track_id grouping
0  Ice Cream (with Selena Gomez)  2J4P46vCFm1rPkNkp9pZWX     kpop
1                       Dynamite  0v1x6rN6JHRapa03JElljE     kpop
2                    THE BADDEST  2V4Fx72svQRxrFvNT1eq5f     kpop

In [443]:
#all to "kpop"
df.loc[df['grouping'].isin(target_and_kpop), 'grouping'] = "kpop"

In [444]:
df.shape

(4618, 3)

In [445]:
df["grouping"].unique()

array(['kpop', 'global', 'billboard'], dtype=object)

In [446]:
def get_lyrics(track_id):
    try:
        lyrics = ""
        with open(lyrics_directory + track_id + ".txt", "r") as f:
            lyrics = f.read()
            
        return lyrics            
    except:
        return None
    
df["lyrics"] = df["track_id"].apply(get_lyrics)

df.shape

(4618, 4)

In [447]:
# stop words
# https://www.kaggle.com/datasets/rowhitswami/stopwords/
stopwords = set()
with open(stopwords_file, "r") as f:
    stopwords = set(f.read().split("\n"))
    
stopwords

{',',
 '>',
 '?',
 'Just',
 'Yes',
 'a',
 'abaft',
 'abafter',
 'abaftest',
 'about',
 'abouter',
 'aboutest',
 'above',
 'abover',
 'abovest',
 'accordingly',
 'aer',
 'aest',
 'afore',
 'after',
 'afterer',
 'afterest',
 'afterward',
 'afterwards',
 'again',
 'against',
 'aid',
 'ain',
 'albeit',
 'all',
 'aller',
 'allest',
 'alls',
 'allyou',
 'almost',
 'along',
 'alongside',
 'already',
 'also',
 'although',
 'always',
 'amid',
 'amidst',
 'among',
 'amongst',
 'an',
 'and',
 'andor',
 'anear',
 'anent',
 'another',
 'any',
 'anybody',
 'anyhow',
 'anyone',
 'anything',
 'anywhere',
 'apart',
 'aparter',
 'apartest',
 'appear',
 'appeared',
 'appearing',
 'appears',
 'appropriate',
 'appropriated',
 'appropriater',
 'appropriates',
 'appropriatest',
 'appropriating',
 'are',
 'ares',
 'around',
 'as',
 'ases',
 'aside',
 'asides',
 'aslant',
 'astraddle',
 'astraddler',
 'astraddlest',
 'astride',
 'astrider',
 'astridest',
 'at',
 'athwart',
 'atop',
 'atween',
 'aught',
 'aught

## Analyze

In [448]:
def is_stopword(word):
    word = word.lower()
    
    if len(word) <= 1:
        return True
    
    # in the list
    if word in stopwords:
        return True
    
    # is Korean
    if ord("가") <= ord(word[0]) <= ord("힣"):
        return True
    
    return False

### Characteristic Keyword
Using TF-IDF

In [449]:
from sklearn.feature_extraction.text import TfidfVectorizer

#### Among global

In [450]:
df_looking = df[df["grouping"].isin(target_and_global)].reset_index(drop=True)

In [451]:
vectorizer = TfidfVectorizer(stop_words=list(stopwords), max_features=1000, min_df=10)

x = vectorizer.fit_transform(df_looking["lyrics"].fillna("")).toarray()

df_tfidf = pd.DataFrame(x, columns=vectorizer.get_feature_names_out()).T

c:\Users\Hiyoko\.conda\envs\data\lib\site-packages\sklearn\feature_extraction\text.py:408: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['vis', 'viser', 'visest', 'yes'] not in stop_words.
  warnings.warn(


In [452]:
threshold = 0.001
counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    tfidf_series = df_tfidf[cnt]
    
    keywords = tfidf_series[tfidf_series > threshold].index.tolist()
    for keyword in keywords:
        counter[keyword] = counter.get(keyword, 0) + 1
        summer[keyword] = summer.get(keyword, 0) + float(tfidf_series[keyword])

In [453]:
def sort_dictionary(dictionary):
    return [(k, dictionary[k]) for k in sorted(dictionary, key=dictionary.get, reverse=True)]

In [454]:
tfidf_counter_global = sort_dictionary(counter)
tfidf_counter_global

[('love', 521),
 ('let', 507),
 ('sorry', 497),
 ('news', 412),
 ('home', 410),
 ('heart', 362),
 ('yes', 345),
 ('eyes', 313),
 ('baby', 311),
 ('feel', 301),
 ('say', 299),
 ('think', 292),
 ('back', 279),
 ('night', 270),
 ('take', 267),
 ('world', 239),
 ('new', 226),
 ('follow', 224),
 ('only', 220),
 ('am', 217),
 ('need', 212),
 ('tell', 206),
 ('life', 202),
 ('leave', 202),
 ('light', 199),
 ('dream', 199),
 ('keep', 195),
 ('room', 190),
 ('give', 179),
 ('way', 177),
 ('end', 171),
 ('mind', 170),
 ('down', 162),
 ('wait', 149),
 ('still', 146),
 ('hands', 143),
 ('child', 142),
 ('show', 140),
 ('dance', 139),
 ('girl', 139),
 ('looking', 136),
 ('care', 135),
 ('price_varies', 133),
 ('contact', 133),
 ('little', 130),
 ('hear', 128),
 ('ah', 128),
 ('okay', 126),
 ('away', 125),
 ('honey', 122),
 ('boy', 121),
 ('beautiful', 121),
 ('sleep', 119),
 ('find', 119),
 ('start', 119),
 ('ready', 118),
 ('feeling', 118),
 ('bad', 117),
 ('stay', 116),
 ('call', 115),
 ('sky', 1

In [455]:
tfidf_summer_global = sort_dictionary(summer)
tfidf_summer_global

[('love', 90.37153562331105),
 ('home', 76.21004040264718),
 ('sorry', 69.1397655218261),
 ('news', 48.08603122812252),
 ('let', 45.65971006638431),
 ('heart', 43.53378986841094),
 ('yes', 39.32657988099398),
 ('baby', 37.152868190550656),
 ('한국', 32.36819854379235),
 ('follow', 32.046654207752745),
 ('eyes', 30.337788713241792),
 ('night', 30.09200698624242),
 ('feel', 28.39620085138629),
 ('dream', 27.485997323149512),
 ('back', 27.444226966689936),
 ('world', 27.138972303382236),
 ('new', 25.668929887759134),
 ('say', 25.19307183864961),
 ('ah', 24.989323963741565),
 ('light', 24.884317238554694),
 ('only', 24.528770918077953),
 ('think', 24.049286804765085),
 ('woo', 23.311984021567397),
 ('room', 22.957403813727545),
 ('am', 22.89032814755495),
 ('dance', 22.81597776759301),
 ('need', 22.554843859626192),
 ('life', 21.359150404595603),
 ('contact', 20.8388989921961),
 ('hot', 20.835045446552304),
 ('give', 20.800300456215705),
 ('boy', 20.55275934228878),
 ('end', 19.7053305786462

#### Among KPOP

In [456]:
df_looking = df[df["grouping"].isin(target_and_kpop)].reset_index(drop=True)

In [457]:
vectorizer = TfidfVectorizer(stop_words=list(stopwords), max_features=1000, min_df=10)

x = vectorizer.fit_transform(df_looking["lyrics"].fillna("")).toarray()

df_tfidf = pd.DataFrame(x, columns=vectorizer.get_feature_names_out()).T

c:\Users\Hiyoko\.conda\envs\data\lib\site-packages\sklearn\feature_extraction\text.py:408: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['vis', 'viser', 'visest', 'yes'] not in stop_words.
  warnings.warn(


In [458]:
threshold = 0.001
counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    tfidf_series = df_tfidf[cnt]
    
    keywords = tfidf_series[tfidf_series > threshold].index.tolist()
    for keyword in keywords:
        counter[keyword] = counter.get(keyword, 0) + 1
        summer[keyword] = summer.get(keyword, 0) + float(tfidf_series[keyword])

In [459]:
tfidf_counter_kpop = sort_dictionary(counter)
tfidf_counter_kpop

[('love', 521),
 ('let', 507),
 ('sorry', 497),
 ('news', 413),
 ('home', 408),
 ('heart', 363),
 ('yes', 345),
 ('eyes', 313),
 ('baby', 312),
 ('feel', 301),
 ('say', 299),
 ('think', 292),
 ('back', 279),
 ('night', 271),
 ('take', 267),
 ('world', 239),
 ('new', 226),
 ('follow', 224),
 ('only', 221),
 ('am', 217),
 ('need', 212),
 ('tell', 207),
 ('life', 202),
 ('leave', 202),
 ('light', 199),
 ('dream', 199),
 ('keep', 195),
 ('room', 190),
 ('give', 179),
 ('way', 177),
 ('end', 171),
 ('mind', 170),
 ('down', 162),
 ('wait', 149),
 ('still', 146),
 ('hands', 144),
 ('child', 142),
 ('show', 140),
 ('dance', 139),
 ('girl', 139),
 ('looking', 136),
 ('care', 135),
 ('price_varies', 133),
 ('contact', 133),
 ('little', 130),
 ('hear', 128),
 ('ah', 128),
 ('away', 125),
 ('okay', 125),
 ('honey', 122),
 ('boy', 121),
 ('beautiful', 121),
 ('sleep', 119),
 ('find', 119),
 ('start', 119),
 ('feeling', 118),
 ('bad', 117),
 ('ready', 117),
 ('stay', 116),
 ('call', 115),
 ('sky', 1

In [460]:
tfidf_summer_kpop = sort_dictionary(summer)
tfidf_summer_kpop

[('love', 93.38607915430586),
 ('home', 67.60988950474074),
 ('sorry', 50.59637894638318),
 ('let', 47.93110110384121),
 ('heart', 41.116791964066365),
 ('yes', 41.10677536323856),
 ('baby', 38.186684222047816),
 ('news', 31.517989144550324),
 ('feel', 31.44896588575648),
 ('night', 31.329232070269644),
 ('say', 29.465943981617627),
 ('back', 28.917235907807306),
 ('only', 27.346261757010232),
 ('eyes', 27.17744214823235),
 ('think', 25.90023701555005),
 ('follow', 25.761256945043133),
 ('need', 25.761205628558344),
 ('world', 25.658269008485153),
 ('한국', 25.315827692846227),
 ('am', 24.95654988991367),
 ('take', 24.1156828940417),
 ('life', 23.881421538952736),
 ('give', 23.697773262598623),
 ('new', 23.122089100039577),
 ('ah', 22.84938734799792),
 ('dream', 22.769037842367304),
 ('light', 22.613825747417657),
 ('dance', 21.8695620276186),
 ('tell', 21.632868387047996),
 ('woo', 21.403899689771514),
 ('boy', 20.841865832124057),
 ('leave', 20.144998389279486),
 ('room', 19.6380575782

### Topic analysis

In [461]:
from gensim.corpora.dictionary import Dictionary
from gensim.models import LdaModel

In [462]:
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis
def save_lda_vis(lda, corpus, dictionary, filename):
    vis = gensimvis.prepare(lda, corpus, dictionary)
    pyLDAvis.save_html(vis, filename)
    
    with open(filename, "r") as f:
        html = f.read()
        
    return html, vis

In [463]:
def pre_process(df_lyrics):
    # tokenize lyrics
    lyrics_processed = df_lyrics.fillna("").str.split()

    for _list in lyrics_processed:
        for cnt in range(len(_list)):
            _list[cnt] = _list[cnt].replace(".", "").replace(",", "").replace("?", "").replace("\\", "").replace("/", "").replace(":", "").lower()
            
            if is_stopword(_list[cnt]):
                _list[cnt] = ""
                
    # remove empty string
    for cnt in range(len(lyrics_processed)):
        while(True):
            try:
                lyrics_processed[cnt].remove("")
            except:
                break

    return lyrics_processed

#### Among global

In [464]:
df_looking = df[df["grouping"].isin(target_and_global)].reset_index(drop=True)

In [465]:
#train model
lyrics_processed = pre_process(df_looking["lyrics"])
dictionary = Dictionary(lyrics_processed)
corpus = [dictionary.doc2bow(text) for text in lyrics_processed]
lda = LdaModel(corpus=corpus, id2word=dictionary, num_topics=100)

all topics

In [466]:
lda_html_global, vis = save_lda_vis(lda, corpus, dictionary, "lda.html")

vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
6     -0.040543  0.050875       1        1  2.347111
37    -0.057145 -0.041267       2        1  2.283469
23    -0.086903 -0.004697       3        1  2.272168
94    -0.130042 -0.072841       4        1  2.260188
68    -0.087211 -0.012996       5        1  2.216441
...         ...       ...     ...      ...       ...
78     0.176725 -0.177973      96        1  0.391231
34     0.044951 -0.021766      97        1  0.389642
20     0.061279  0.065694      98        1  0.368482
49     0.123252  0.037815      99        1  0.233179
31     0.072427  0.023673     100        1  0.202957

[100 rows x 5 columns], topic_info=        Term         Freq        Total  Category  logprob  loglift
7603  labour  5375.000000  5375.000000   Default  30.0000  30.0000
280    child  5472.000000  5472.000000   Default  29.0000  29.0000
0       baby  6153.000000  6153.000000   Default  28.0000  28.0000
425    drunk  2749.000000  2749.000000   Default  27.0000  27.0000
494     cake  2285.000000  2285.000000   Default  26.0000  26.0000
...      ...          ...          ...       ...      ...      ...
9      can't     6.919396  4529.057125  Topic100  -5.1335  -0.2840
321     tell     6.365884  2650.779962  Topic100  -5.2168   0.1683
232      say     5.741889  3695.042849  Topic100  -5.3200  -0.2670
259     girl     5.557362  2532.371887  Topic100  -5.3527   0.0781
58      only     5.438066  2785.431597  Topic100  -5.3744  -0.0388

[6136 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
7266      63  0.619769    "cuz"
7266      72  0.206590    "cuz"
15845      5  0.107068   "happy
15845     41  0.749474   "happy
12568     18  0.071385  "hello"
...      ...       ...      ...
629       24  0.894823       和을
3872       2  0.896466       和집
4415      65  0.978196       和하
2617      24  0.038219      日本語
2617      67  0.879044      日本語

[49824 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[7, 38, 24, 95, 69, 44, 72, 26, 96, 66, 65, 41, 19, 48, 14, 45, 90, 68, 94, 74, 37, 98, 23, 75, 59, 85, 3, 80, 73, 61, 30, 17, 97, 92, 99, 70, 25, 34, 56, 55, 40, 93, 8, 6, 77, 28, 49, 1, 12, 60, 43, 54, 87, 2, 46, 63, 100, 53, 62, 29, 81, 16, 83, 27, 78, 33, 71, 15, 9, 36, 51, 20, 88, 86, 31, 39, 10, 84, 58, 47, 89, 52, 57, 91, 67, 4, 82, 5, 22, 42, 18, 76, 13, 11, 64, 79, 35, 21, 50, 32])

what topics are in kpop?

In [467]:
threshold = 0.3

counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    topics = lda.get_document_topics(corpus[cnt], minimum_probability=0)
    
    for topic in topics:
        if topic[1] > threshold:
            counter[topic[0]] = counter.get(topic[0], 0) + 1
            
        summer[topic[0]] = summer.get(topic[0], 0) + float(topic[1])

In [468]:
_lda_counter_global = sort_dictionary(counter)
lda_counter_global = []
for tup in _lda_counter_global:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_counter_global.append(new_tup)
    
lda_counter_global

[[94,
  89,
  [('news', 0.043080505),
   ('music', 0.025731675),
   ('heart', 0.023725796),
   ('sorry', 0.020438774),
   ('follow', 0.020045882),
   ('only', 0.013392063),
   ('need', 0.011798945),
   ("can't", 0.011496064),
   ('say', 0.010558757),
   ('happy', 0.010070088)]],
 [37,
  45,
  [('love', 0.3500582),
   ('yes', 0.014827028),
   ('bomb', 0.013221377),
   ('am', 0.010880957),
   ('crazy', 0.009132985),
   ('night', 0.007814854),
   ('generating', 0.007749803),
   ('nice', 0.007672508),
   ('heart', 0.007433877),
   ('believe', 0.007296011)]],
 [36,
  43,
  [('home', 0.35882828),
   ('shut', 0.037717115),
   ('mom', 0.022556508),
   ('comment', 0.021304948),
   ('love', 0.012355566),
   ("let's", 0.010586113),
   ('girlfriend', 0.010239532),
   ('baby', 0.009230468),
   ("can't", 0.0074868677),
   ('youth', 0.0070070573)]],
 [47,
  28,
  [('sorry', 0.05083636),
   ('only', 0.017859977),
   ("can't", 0.012372094),
   ('love', 0.012263773),
   ('tags', 0.012217484),
   ('shy',

In [469]:
_lda_summer_global = sort_dictionary(summer)
lda_summer_global = []
for tup in _lda_summer_global:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_summer_global.append(new_tup)
    
lda_summer_global

[[94,
  97.18348057768162,
  [('news', 0.043080505),
   ('music', 0.025731675),
   ('heart', 0.023725796),
   ('sorry', 0.020438774),
   ('follow', 0.020045882),
   ('only', 0.013392063),
   ('need', 0.011798945),
   ("can't", 0.011496064),
   ('say', 0.010558757),
   ('happy', 0.010070088)]],
 [37,
  50.092006700402635,
  [('love', 0.3500582),
   ('yes', 0.014827028),
   ('bomb', 0.013221377),
   ('am', 0.010880957),
   ('crazy', 0.009132985),
   ('night', 0.007814854),
   ('generating', 0.007749803),
   ('nice', 0.007672508),
   ('heart', 0.007433877),
   ('believe', 0.007296011)]],
 [36,
  46.42961788350385,
  [('home', 0.35882828),
   ('shut', 0.037717115),
   ('mom', 0.022556508),
   ('comment', 0.021304948),
   ('love', 0.012355566),
   ("let's", 0.010586113),
   ('girlfriend', 0.010239532),
   ('baby', 0.009230468),
   ("can't", 0.0074868677),
   ('youth', 0.0070070573)]],
 [47,
  38.244720211875574,
  [('sorry', 0.05083636),
   ('only', 0.017859977),
   ("can't", 0.012372094),


#### Among KPOP

In [470]:
df_looking = df[df["grouping"].isin(target_and_kpop)].reset_index(drop=True)

In [471]:
#train model
lyrics_processed = pre_process(df_looking["lyrics"])
dictionary = Dictionary(lyrics_processed)
corpus = [dictionary.doc2bow(text) for text in lyrics_processed]
lda = LdaModel(corpus=corpus, id2word=dictionary, num_topics=100)

# observe topics
topics = lda.print_topics()

In [472]:
threshold = 0.3

counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    topics = lda.get_document_topics(corpus[cnt], minimum_probability=0)
    
    for topic in topics:
        if topic[1] > threshold:
            counter[topic[0]] = counter.get(topic[0], 0) + 1
            
        summer[topic[0]] = summer.get(topic[0], 0) + float(topic[1])


In [473]:
lda_html_kpop, vis = save_lda_vis(lda, corpus, dictionary, "lda.html")

vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
78    -0.491120 -0.023059       1        1  3.360412
4     -0.040538  0.153812       2        1  2.463030
9      0.040514  0.044673       3        1  2.292450
62     0.009217  0.070051       4        1  2.166460
71     0.018115  0.092098       5        1  2.104700
...         ...       ...     ...      ...       ...
88    -0.413129 -0.015255      96        1  0.317639
25    -0.018583 -0.083598      97        1  0.307408
85    -0.001912 -0.069629      98        1  0.306021
67     0.020462 -0.091719      99        1  0.194730
5     -0.012054 -0.093662     100        1  0.087696

[100 rows x 5 columns], topic_info=      Term         Freq        Total  Category  logprob  loglift
280  child  4885.000000  4885.000000   Default  30.0000  30.0000
425  drunk  2395.000000  2395.000000   Default  29.0000  29.0000
494   cake  1259.000000  1259.000000   Default  28.0000  28.0000
101  dance  1218.000000  1218.000000   Default  27.0000  27.0000
120   home  2102.000000  2102.000000   Default  26.0000  26.0000
..     ...          ...          ...       ...      ...      ...
932   last     0.514837   161.231896  Topic100  -5.5025   1.2923
901    ())     0.487556    72.287432  Topic100  -5.5569   2.0400
917   blue     0.477132   126.492854  Topic100  -5.5785   1.4589
293  leave     0.474402   377.861801  Topic100  -5.5843   0.3588
398  dream     0.470016   413.808793  Topic100  -5.5936   0.2587

[6525 rows x 6 columns], token_table=       Topic      Freq  Term
term                        
5866      15  0.065723    !!
5866      26  0.131445    !!
5866      51  0.262890    !!
5866      53  0.065723    !!
5866      81  0.328613    !!
...      ...       ...   ...
4295      87  0.570127    誰も
9717      37  0.616934  進むほど
4296      87  0.571297    闇夜
10127     22  0.274431   飲み干
10127     27  0.548862   飲み干

[29735 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[79, 5, 10, 63, 72, 13, 24, 77, 8, 1, 2, 29, 51, 65, 95, 34, 28, 42, 83, 31, 37, 99, 48, 76, 27, 59, 74, 36, 75, 62, 55, 67, 85, 16, 11, 78, 45, 40, 41, 96, 19, 90, 15, 57, 12, 60, 17, 50, 43, 3, 25, 97, 54, 47, 52, 80, 49, 87, 100, 84, 64, 33, 46, 39, 93, 32, 98, 92, 82, 61, 9, 7, 18, 91, 35, 71, 44, 23, 69, 94, 53, 70, 66, 21, 38, 81, 73, 14, 20, 4, 58, 88, 56, 22, 30, 89, 26, 86, 68, 6])

In [474]:
_lda_counter_kpop = sort_dictionary(counter)
lda_counter_kpop = []
for tup in _lda_counter_kpop:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_counter_kpop.append(new_tup)
    
lda_counter_kpop

[[71,
  41,
  [('love', 0.07941954),
   ('best', 0.046812844),
   ('detail', 0.037148025),
   ('work', 0.015623299),
   ('yes', 0.012461519),
   ('heart', 0.011305288),
   ('say', 0.010987526),
   ('need', 0.009074914),
   ('dam', 0.008945391),
   ('take', 0.008818261)]],
 [23,
  39,
  [('drunk', 0.05279879),
   ('love', 0.033399038),
   ('home', 0.021012126),
   ('eyes', 0.01456852),
   ('feel', 0.011516005),
   ('sorry', 0.010750648),
   ('child', 0.010408275),
   ('ti', 0.008351293),
   ("can't", 0.0072009787),
   ('heart', 0.0068408363)]],
 [62,
  34,
  [('love', 0.08801573),
   ('pop', 0.047247875),
   ('reale', 0.03518533),
   ('give', 0.01787542),
   ('crazy', 0.015093938),
   ('still', 0.009403442),
   ('room', 0.008603292),
   ('mariachi', 0.00805962),
   ('el', 0.007938149),
   ('dream', 0.0078386795)]],
 [0,
  31,
  [('love', 0.13010024),
   ('heart', 0.010538178),
   ("can't", 0.009427025),
   ('yes', 0.009363636),
   ('play', 0.00929487),
   ('real', 0.008606987),
   ('bab

In [475]:
_lda_summer_kpop = sort_dictionary(summer)
lda_summer_kpop = []
for tup in _lda_summer_kpop:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_summer_kpop.append(new_tup)
    
lda_summer_kpop

[[71,
  39.122559087441914,
  [('love', 0.07941954),
   ('best', 0.046812844),
   ('detail', 0.037148025),
   ('work', 0.015623299),
   ('yes', 0.012461519),
   ('heart', 0.011305288),
   ('say', 0.010987526),
   ('need', 0.009074914),
   ('dam', 0.008945391),
   ('take', 0.008818261)]],
 [23,
  35.53663166861588,
  [('drunk', 0.05279879),
   ('love', 0.033399038),
   ('home', 0.021012126),
   ('eyes', 0.01456852),
   ('feel', 0.011516005),
   ('sorry', 0.010750648),
   ('child', 0.010408275),
   ('ti', 0.008351293),
   ("can't", 0.0072009787),
   ('heart', 0.0068408363)]],
 [0,
  34.38584517859999,
  [('love', 0.13010024),
   ('heart', 0.010538178),
   ("can't", 0.009427025),
   ('yes', 0.009363636),
   ('play', 0.00929487),
   ('real', 0.008606987),
   ('baby', 0.008299252),
   ('tell', 0.008208396),
   ('feel', 0.008082967),
   ('generating', 0.008006069)]],
 [62,
  34.22077450620236,
  [('love', 0.08801573),
   ('pop', 0.047247875),
   ('reale', 0.03518533),
   ('give', 0.01787542)

### Emotion analysis
Emotions:  
fear
anger
anticipation
trust
surprise
positive
negative
sadness
disgust
joy

In [476]:
import numpy as np

In [477]:
emotions = [
    "anger",
    "anticipation",
    "disgust",
    "fear",
    "joy",
    "negative",	
    "positive",
    "sadness",
    "surprise",	
    "trust",
]

In [478]:
df_nrc = pd.read_csv("NRC.txt", sep="\t", names=["word", "emotion", "amount"])

words_to_emotions = {}

for _, row in df_nrc.iterrows():
    words_to_emotions[row["word"]] = words_to_emotions.get(row["word"], np.zeros((10, 1)))
    words_to_emotions[row["word"]][emotions.index(row["emotion"])] = row["amount"]

In [479]:
df_emotion = df.copy()
for emotion in emotions:
    df_emotion[emotion] = 0

In [480]:
for cnt in range(len(df)):
    lyrics = df["lyrics"][cnt]

    if type(lyrics) != str:
        continue

    emotion_this = np.zeros((10, 1))

    for word in lyrics.split():
        if word in words_to_emotions:
            emotion_this += words_to_emotions[word]
            
    if np.linalg.norm(emotion_this) != 0:
        emotion_this /= np.linalg.norm(emotion_this)
        
    for emotion in emotions:
        df_emotion[emotion][cnt] = emotion_this[emotions.index(emotion)]

C:\Users\Hiyoko\AppData\Local\Temp\ipykernel_8924\3182639529.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_emotion[emotion][cnt] = emotion_this[emotions.index(emotion)]
C:\Users\Hiyoko\AppData\Local\Temp\ipykernel_8924\3182639529.py:17: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[0.06561363]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  df_emotion[emotion][cnt] = emotion_this[emotions.index(emotion)]
C:\Users\Hiyoko\AppData\Local\Temp\ipykernel_8924\3182639529.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-

In [481]:
df_emotion_global = df_emotion[df_emotion["grouping"].isin(global_group)]
mean_emotion_global = df_emotion_global[emotions].mean()
normalized_mean_emotion_global = mean_emotion_global / np.linalg.norm(mean_emotion_global)

df_emotion_kpop = df_emotion[df_emotion["grouping"].isin(kpop_group)]
mean_emotion_kpop = df_emotion_kpop[emotions].mean()
normalized_mean_emotion_kpop = mean_emotion_kpop / np.linalg.norm(mean_emotion_kpop)

df_emotion_target = df_emotion[df_emotion["grouping"] == target_group]
mean_emotion_target = df_emotion_target[emotions].mean()
normalized_mean_emotion_target = mean_emotion_target / np.linalg.norm(mean_emotion_target)

In [482]:
normalized_mean_emotion_target

anger           0.157894
anticipation    0.321387
disgust         0.099041
fear            0.207745
joy             0.388888
negative        0.358769
positive        0.626679
sadness         0.217019
surprise        0.166724
trust           0.266915
dtype: float64

against global

In [483]:
emotion_percentage_global = (normalized_mean_emotion_target - normalized_mean_emotion_global) / normalized_mean_emotion_global * 100

emotion_percentage_global

anger          -25.268986
anticipation     8.704336
disgust        -27.502075
fear           -11.956912
joy             12.735731
negative       -22.729707
positive        17.274200
sadness        -15.694206
surprise        -2.115851
trust           -4.557240
dtype: float64

against KPOP

In [484]:
emotion_percentage_kpop = (normalized_mean_emotion_target - normalized_mean_emotion_kpop) / normalized_mean_emotion_kpop * 100

emotion_percentage_kpop

anger           0.0
anticipation    0.0
disgust         0.0
fear            0.0
joy             0.0
negative        0.0
positive        0.0
sadness         0.0
surprise        0.0
trust           0.0
dtype: float64

## Save Data

In [485]:
# to float
for _sum in lda_summer_global:
    _sum[2] = [(tup[0], float(tup[1])) for tup in _sum[2]]
    
for _sum in lda_summer_kpop:
    _sum[2] = [(tup[0], float(tup[1])) for tup in _sum[2]]
    
for count in lda_counter_global:
    count[2] = [(tup[0], float(tup[1])) for tup in count[2]]

for count in lda_counter_kpop:
    count[2] = [(tup[0], float(tup[1])) for tup in count[2]]

In [486]:
json_data = {
    "tfidf_counter_global": tfidf_counter_global,
    "tfidf_summer_global": tfidf_summer_global,
    "tfidf_counter_kpop": tfidf_counter_kpop,
    "tfidf_summer_kpop": tfidf_summer_kpop,
    "lda_counter_global": lda_counter_global,
    "lda_summer_global": lda_summer_global,
    "lda_counter_kpop": lda_counter_kpop,
    "lda_summer_kpop": lda_summer_kpop,
    "lda_html_global": lda_html_global,
    "lda_html_kpop": lda_html_kpop,
    "normalized_mean_emotion_target": normalized_mean_emotion_target.astype(float).tolist(),
    "emotion_percentage_global": emotion_percentage_global.astype(float).tolist(),
    "emotion_percentage_kpop": emotion_percentage_kpop.astype(float).tolist(),
}

In [487]:
import json
with open("data_"+ target_group +".json", "w") as f:
    json.dump(json_data, f)